# A Primer on Prior Networks

Harvard Fall 2019 Applied Math 207 Term Project

Authors (alphabetically ordered): Simon Batzner, Theo Guenais, Rylan Schaeffer, Dimitris Vamvourellis

Paper: [Predictive Uncertainty Estimation via Prior Networks](https://papers.nips.cc/paper/7936-predictive-uncertainty-estimation-via-prior-networks.pdf)


## Section 1: Problem Statement

Deep Learning has become one of the most successful and widely used methods in Machine Learning. While Neural Networks obtain very high accuracy on a wide variety of tasks, they still only give point estimates rather than predictive distributions. This results in a lack of uncertainty estimates, leading to models that can be over-confident. 

## Section 2: Context/Scope

Well-calibrated and reliable uncertainty estimates are of crucial importance in a series of high-stakes applications, such as e.g. medical machine learning, autonomous driving, or legal decisions. Without predictive uncertainty, no assessment on the model's trustability can be made, deeming neural networks insuitable for a variety of problems. With access to uncertainty estimates however, if a model predicts a high-stakes result with large uncertainty, the decision can be deferred to an expert, such as e.g. a human physician in the example of a medical application. 

## Section 3: Existing Work and Contribution

### Existing Work

Other approaches have been focused on Bayesian Neural Networks [1, 2], a class of neural networks that estimates distributions of the neural network weights. The resulting posterior is often computationally intractable and a series of assumptions has to be made in practice. Another widely used method is that of Monte-Carlo Dropout, introduced by Gal [3], which estimates uncertainty by performing a series of forward passes through the network with a different set of nodes dropped out, thereby approximating an ensemble. In addition to MC-Dropout, a series of other ensemble-based methods are used, in particular the method of Deep Ensembles has seen wide acceptance [4]. Furthermore, different approaches have been proposed [5, 6] that aim to minimize the KL-Divergence to a sharp posterior on seen data (in-domain) and also to flat posterior for unseen data (out-of-domain). 

### Contribution

This paper is trying to address a problem that is inherent to the above approaches, namely that they mix different types of uncertainty, which according to the authors, should be addressed a separate entities. These three are: 

1. model uncertainty: a measure of how uncertain the model's parameters are given the training data; this can be explained away given more data. 
2. data uncertainty: this is a type of uncertainty stemming from label noise, it therefore cannot be reduced with more data, no matter how many data are fed to a model, if the noise in the underlying training data is too large, the model will never be able to move past this noise uncertainty. 
3. distributional uncertainty: this type of uncertainty comes up when training and test data come from different distributions (called dataset shift). Since the model has only seen data from the training distribution, it cannot accurately predict on the test data. 

The authors argue that existing approches mix in distribution uncertainty either with model or data uncertainty, but that instead this source of uncertainty should be treated as separate. They then propose a new type of neural network which they call Prior Networks, which explicitly treat distributional uncertainty. Finally, they apply this network to different classification problems and measure performance on the tasks of detecting out-of-distribution samples and misclassification and are shown to perform better than previous methods on the MNIST and CIFAR-10 data sets. 

[1] David JC MacKay, “A practical bayesian framework for backpropagation networks,” Neural
computation, vol. 4, no. 3, pp. 448–472, 1992

[2] Radford M. Neal, Bayesian learning for neural networks, Springer Science & Business Media,
1996

[3] Yarin Gal and Zoubin Ghahramani, “Dropout as a Bayesian Approximation: Representing
Model Uncertainty in Deep Learning,” in Proc. 33rd International Conference on Machine
Learning (ICML-16), 2016

[4] B. Lakshminarayanan, A. Pritzel, and C. Blundell, “Simple and Scalable Predictive Uncertainty
Estimation using Deep Ensembles

[5] A. Malinin, A. Ragni, M.J.F. Gales, and K.M. Knill, “Incorporating Uncertainty into Deep
Learning for Spoken Language Assessment,

[6] Kimin Lee, Honglak Lee, Kibok Lee, and Jinwoo Shin, “Training confidence-calibrated
classifiers for detecting out-of-distribution samples,” International Conference on Learning
Representations, 2018.

## Section 4: Technical Content

## Section 5: Experiments

In [1]:
# import packages
import numpy as np
import torch
from matplotlib import pyplot as plt
%matplotlib inline
from utils import data, measures, models, plot, run

### Ordinarily Trained Discriminative Classifiers Have No Distributional Uncertainty

The typical lifecycle of a machine learning model consists of splitting one's data into two sets, the training dataset and the test dataset, training a model using the training dataset before evaluating the model on the test dataset. Once trained, the model can be used for inference given new input data. However, this naive approach can be dangerous. Given new input data sampled from a drastically different distribution than the training  distribution, the model might make confident, but incorrect predictions.

To demonstrate this, suppose a medical study identifies that breast cancer patients were cured by one of three treatment plans, and we're recruited to train a model that recommend a treatment plan for a new patient. For simplicity, we'll assume that each patient has two features of interest (e.g. age, BMI) that are predictive of the best treatment for that patient. The dataset might look like the following.

In [2]:
train_data = data.create_data(
        create_data_functions=[
            data.create_data_mixture_of_gaussians,
        ],
        functions_args=[
            data.mog_three_in_distribution
        ])

In [3]:
labels_np = train_data['targets'].numpy()
samples_np = train_data['samples'].numpy()
train_labels_idx = np.where(labels_np != 3)[0]
x_train_np = samples_np[train_labels_idx]
y_train_np = labels_np[train_labels_idx]

labels_names = ['Cured by Treatment 1', 'Cured by Treatment 2', 'Cured by Treatment 3', 'New Patient Data']

In [4]:
plot.plot_training_data(
    samples=train_data['samples'].numpy(),
    labels=train_data['targets'].numpy(),
    labels_names=labels_names,
    plot_title='Training Data',
    xaxis=dict(title='Patient Feature 1 (e.g. age)'),
    yaxis=dict(title='Patient Feature 2 (e.g. BMI)')
)

This looks like a solvable problem! We decide to model these three clusters using a categorical distribution and we train a model to predict the correct class.

In [5]:
# create the model, optimizer, training data
model = run.create_model(in_dim=2, out_dim=3, n_per_hidden_layer=[50], args={})
optimizer = run.create_optimizer(model=model, args={'lr': 0.001})
loss_fn = run.create_loss_fn(loss_fn_str='kl', args={})

In [6]:
# fit the model
model, optimizer, training_loss = run.train_model(
    model=model,
    optimizer=optimizer,
    loss_fn=loss_fn,
    train_data=train_data,
    args={},
    n_epochs=1000,
    batch_size=32)

In [7]:
# plot the training loss
plot.plot_training_loss(training_loss=training_loss)

Looks good! But now, suppose that a medical hospital sends us new patient data that looks unlike anything we've previously seen. What should the model recommend?

In [8]:
new_data = data.create_data(
    create_data_functions=[data.create_data_mixture_of_gaussians,],
    functions_args=[data.mog_three_in_distribution_one_out])
plot.plot_training_data(
    samples=new_data['samples'].numpy(),
    labels=new_data['targets'].numpy(),
    labels_names=labels_names,
    plot_title='Training Data',
    xaxis=dict(title='Patient Feature 1 (e.g. age)'),
    yaxis=dict(title='Patient Feature 2 (e.g. BMI)')
)

Because this new patient data looks nothing like the training data, we would want the model to be highly uncertain. However, when we ask the model to predict the appropriate treatment for the new patients, as the below code demonstrates, the model is actually strongly confident that the correct solution is to prescribe Treatment 2.

In [9]:
new_patient_data_indices = new_data['targets'] == 3
new_patient_samples = new_data['samples'][new_patient_data_indices]
new_patient_model_output = model(new_patient_samples)
print(np.round(new_patient_model_output['y_pred'].detach().numpy(), 3))

[[0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0.

To understand why the model classifies the new patient data with the closest training data class, we visualize the decision surface of the model by calculating the entropy of the predicted probabilities vector, which is a measure of the total uncertainty in the predictions of a model. We add the three training classes as well as the new patient data above the decision surface. As we can see the model makes very confident predictions ever far away from training data (entropy is very low). The model makes uncertain predictions (high entropy) only in between the classes as well as in the middle of the data. Hence, the model does not account for distributional uncertainty. In other words, if the model is given test data which are not drawn from the same distribution as training data, it will still make very confident predictions (low entropy probabilities vector) which may well be utterly wrong.

In [10]:
#please rerun this to create interactive 3D plot
plot.plot_decision_surface(model=model,
                           samples=new_data['samples'],
                           labels=new_data['targets'],
                           labels_names=labels_names,
                           z_fn=measures.entropy_categorical,
                           x_axis_title='Patient Feature 1 (e.g. age)',
                           y_axis_title='Patient Feature 2 (e.g. BMI)',
                           z_axis_title='Predicted Class Entropy'
                          )

### Modified Loss Function/Training Curriculum Gives Classifier Distributional Uncertainty

Below, we are fitting a Dirichlet Prior Network. According to the methodology described in the paper, to train this model both the in-distribution and the out-of-distribution targets must be defined. Hence, we use the same training data as the in-distribution data for which we know the labels. The labels of the new patient data are not known and are far from training data so we use these data points as the out-of-distribution data to train our model. Then, we visualize the model's behaviour both in regions of in and out of distribution data. 

The model makes condifent predictions (low-entropy) in regions dominated by each class. However, now the model makes totally uncertain predictions in the region where we defined that data are out-of-distribution. On this region, as well as in the rest of regions between the classes and away from training data, the entropy attains its maximum value. In other words, the Prior Network assigns a probability of 1/3 to each class, which is a more rational decision given that data from such regions are assumed to be out-of-distribution and we cannot be certain of the class they belong to.

The last figure is a plot of the Mutual Information between the label and the expected categorical predicted by the network. As mentioned in the paper, this is a measure of the distributional uncertainty. Particularly, it is the difference between the total uncertainty and the expected data uncertainty. As it can be observed, the mutual information curve has similar shape to the entropy curve. However, the mutual information is zero in the middle of the three classes, since the uncertainty in this region arises due to class overlap and not due to the fact that this region is considered out-of-domain.

In [11]:
#please run this cell to generate interactive 3D plot
model, optimizer, training_loss = run.train_model(
    model=model,
    optimizer=optimizer,
    loss_fn=loss_fn,
    train_data=new_data, #TRAIN WITH IN AND OUT OF DISTRIBUTION
    args={},
    n_epochs=1000,
    batch_size=128)

In [12]:
plot.plot_training_loss(training_loss=training_loss)

In [13]:
#please rerun this to create interactive 3D plot
plot.plot_decision_surface(model=model,
                           samples=new_data['samples'],
                           labels=new_data['targets'],
                           labels_names=labels_names,
                           z_fn=measures.entropy_categorical,
                           x_axis_title='Patient Feature 1 (e.g. age)',
                           y_axis_title='Patient Feature 2 (e.g. BMI)',
                           z_axis_title='Predicted Class Entropy'
                          )

In [14]:
#please rerun this to create interactive 3D plot
plot.plot_MI(model=model,
            samples=new_data['samples'],
            labels=new_data['targets'],
            labels_names=labels_names,
            x_axis_title='Patient Feature 1 (e.g. age)',
            y_axis_title='Patient Feature 2 (e.g. BMI)',
            )

## Experiments with different OOD shapes

### OOD as a ring around the data

To train a Prior Network, the multi-task objective defined in the paper, requires samples from the out-of-domain distribution. In practical terms, this is unknown and samples are unavailable. One solution is to synthetically generate points on the boundary of the in-domain region. In two dimensions where data can be visualized, this is possible. A sensible choice is to create an out-of-domain distribution which forms a ring around the training data. As a result, any test data on our out of the ring are assumed to be out-of-distribution.

By osberving the entropy and the mutual information plots, it is evident  that the model makes confident predictions within the ring (entropy is minimized apart from the center where classes overlap), whereas the model makes uncertain predictions outside the ring (entropy and mutual information are maximized).

Again, the entropy is high in the middle of the classes whereas mutual information is low. This is because the uncertainty in this region arises due to class overlap (data uncertainty) and not due to lack of training data.

In [15]:
#create the data
train_data_ring = data.create_data(
    create_data_functions=[
        data.create_data_spherical_shells,
        data.create_data_mixture_of_gaussians,
    ],
    functions_args=[
        data.rings,
        data.mog_three_in_distribution_overlap
    ])
plot.plot_training_data(
    samples=train_data_ring['samples'].numpy(),
    labels=train_data_ring['targets'].numpy(),
    labels_names=labels_names,
    plot_title='Training Data',
    xaxis=dict(title='Patient Feature 1 (e.g. age)'),
    yaxis=dict(title='Patient Feature 2 (e.g. BMI)')
)

In [16]:
model, optimizer, training_loss = run.train_model(
    model=model,
    optimizer=optimizer,
    loss_fn=loss_fn,
    train_data=train_data_ring, #TRAIN WITH IN AND OUT OF DISTRIBUTION
    args={},
    n_epochs=1000,
    batch_size=128)

In [17]:
plot.plot_training_loss(training_loss=training_loss)

In [18]:
#please rerun this to create interactive 3D plot
plot.plot_decision_surface(model=model,
                           samples=train_data_ring['samples'],
                           labels=train_data_ring['targets'],
                           labels_names=labels_names,
                           z_fn=measures.entropy_categorical,
                           x_axis_title='Patient Feature 1 (e.g. age)',
                           y_axis_title='Patient Feature 2 (e.g. BMI)',
                           z_axis_title='Predicted Class Entropy'
                          )

In [19]:
#please rerun this to create interactive 3D plot
plot.plot_MI(model=model,
            samples=train_data_ring['samples'],
            labels=train_data_ring['targets'],
            labels_names=labels_names,
            x_axis_title='Patient Feature 1 (e.g. age)',
            y_axis_title='Patient Feature 2 (e.g. BMI)',
            )

### Interpolation: OOD in the middle of the data

In other cases, we might not have any data in the region in between the classes. Consequently, we may want our classifier to refrain from making confident predictions in this region since without any data, we are quite uncertain of the class that these cases belong to. 

Hence, we can generate points from within the inner boundary of the in-domain region to form the OOD data needed to train a Prior Network. The resulting model is now uncertain when interpolating. This is confirmed by the fact that both the entropy and the mutual information are maximized in the middle of the three classes, a region which we specifically assumed to be out-of-domain.

In [20]:
train_data_interpolation = data.create_data(
    create_data_functions=[
        data.create_data_mixture_of_gaussians,
    ],
    functions_args=[
        data.mog_ood_in_middle_no_overlap
    ])
plot.plot_training_data(
    samples=train_data_interpolation['samples'].numpy(),
    labels=train_data_interpolation['targets'].numpy(),
    labels_names=labels_names,
    plot_title='Training Data',
    xaxis=dict(title='Patient Feature 1 (e.g. age)'),
    yaxis=dict(title='Patient Feature 2 (e.g. BMI)')
)

In [21]:
#please run this cell to generate interactive 3D plot
model, optimizer, training_loss = run.train_model(
    model=model,
    optimizer=optimizer,
    loss_fn=loss_fn,
    train_data=train_data_interpolation, #TRAIN WITH IN AND OUT OF DISTRIBUTION
    args={},
    n_epochs=1000,
    batch_size=128)

In [22]:
#please rerun this to create interactive 3D plot
plot.plot_decision_surface(model=model,
                           samples=train_data_interpolation['samples'],
                           labels=train_data_interpolation['targets'],
                           labels_names=labels_names,
                           z_fn=measures.entropy_categorical,
                           x_axis_title='Patient Feature 1 (e.g. age)',
                           y_axis_title='Patient Feature 2 (e.g. BMI)',
                           z_axis_title='Predicted Class Entropy'
                          )

In [23]:
#please rerun this to create interactive 3D plot
plot.plot_MI(model=model,
            samples=train_data_interpolation['samples'],
            labels=train_data_interpolation['targets'],
            labels_names=labels_names,
            x_axis_title='Patient Feature 1 (e.g. age)',
            y_axis_title='Patient Feature 2 (e.g. BMI)',
            )

## Section 6: Evaluation

Disclaimer: The follow is Rylan's opinion and the other authors of this notebook may or may not agree with his perspective.

1. While the notion that the total uncertainty has distinct sources makes sense, I disagree with the specific decomposition chosen by Malinin and Gales. The correct framework should be that if we have training data $D = \{(x_i, y_i) \}_{i=1}^N$ and are asked to learn a model parameterized by $\theta$ that we then subsequently use to predict $y^*$ for a given test point $x^*$, the distribution we are interested in is:

$$p(y^*, x^*, \theta|D) $$

This distribution can be factored into the three distinct source of uncertainty:

$$p(y^*, x^*, \theta|D) = p(y^*, x^*|D)p(y^*|x^*, \theta) p(\theta|D) $$

where the first is the distributional uncertainty i.e. how consistent are $y^*, x^*$ with the training data, the second is the predictive uncertainty i.e. how uncertain is the model in the inferred value $y^*$, and the third is the parameter uncertainty i.e. how uncertain we are regarding the parameters $\theta$. As a small note, Malinin and Gales use the term "data" uncertainty for what I call "predictive" uncertainty, which I disagree with, since the source of the uncertainty is the model's prediction of $y^*$ and is not necessarily inherent to the data. Similary, I think "model" uncertainty is unclear, so I use the term parameter uncertainty. Returning to my main objection, rather than using my suggested factorization, Malinin and Gales use the following factorization (Equation 4):

$$P(\omega_c|x^*, D) = \int \int d\mu \, d\theta \,p(\omega_c|\mu) p(\mu|x^*, \theta) p(\theta|D) $$ 

where $\omega_c$ is the predicted class of the model and $\mu$ are the parameters output by the model that parameterizat the distribution for $\omega_c$. Not only is this notation unnecessarily unclear, but it also fails to capture the quantities we care about. First, the left hand side has no dependence on the model's parameters $\theta$ since Malinin has marginalized them out. One could argue that the model parameters are unimportant so long as we marginalize them out, but if we do, then the so-called parameter uncertainty ceases to be relevant. Second, the notion of distributional uncertainty is that $x^*$ (or $(x^*, y^*)$ jointly) may differ from $D$, but his distributional uncertainty term $p(\mu|x^*, \theta)$ fails to relate $x^*$ to $D$ whatsoever. And his data uncertainty term, in addition to being marginalized out, has nothing to do with the data; rather, it expressed the model's assumption that $\mu$ parameterizes $\omega_c$, which is a modeling choice.

I also think that two of the three reviewers who approved this paper for NeurIPS failed to thoroughly vet this paper. Reviewer 1 seems to be the only one who read the paper, correctly pointing out several key flaws:

1. "There is no model uncertainty in this paper as a dirac is used for the model prior, so why spend time talkimg about it?"

2. "They effectively eliminate the whole hierarchy that was introduced in Section 3. It makes the whole story about Bayesian inference a bit overboard: in fact, there is very little to do with Bayes here. Indeed, it's not stated explicitly that I could see, but p(w_c|mu) = mu_c and so, fact, everything simplifies to eq (12) which shows that essentially the prediction is just a softmax over a neural network applied to the inputs in eq (13)."

3. "Whereas Malinin et al, 2017 use (14) to fit Gaussians, this work use it to fit categorical data. That appears to be the main distinction to prior work."

In contrast to Reviewer 1's careful eye, Reviewer 2 wrote, "The paper is also original since it is quite different from previous Bayesian approach by explicitly parametrize the distribution by DNN," which is laughable since the network is predicting classes using a softmax. Additionally, the notion of using neural networks to parameterize distributions has a long history; a [1994 review of classification methods using neural networks](https://www.jstor.org/stable/2346118?seq=1) references several approaches to parameterize distributions using neural networks, and [Williams 1992](https://link.springer.com/article/10.1007/BF00992696) introduced two methods (i.e. REINFORCE and the reparameterization trick) for training neural networks to output probability distributions. Also, a quick google search revealed that [Neural Adaptive Sequential Monte Carlo](https://papers.nips.cc/paper/5961-neural-adaptive-sequential-monte-carlo.pdf) from 2015 (3 years prior!) proposes using neural networks to parameterize probability distributions, albeit in the context of Monte Carlo sampling methods.

Lastly, Reviewer 3 wrote, "This is a very well written paper with a thorough survey of existing approaches, providing a valuable reading list." Malinin and Gales make **one** reference to prior work on studying mismatch between training and testing data distributions, writing:

"Distributional uncertainty arises due to mismatch between the training and test distributions (also called dataset shift [24]) - a situation which often arises for real world problems."

That citation 24, [Quiñonero-Candela's Dataset Shift in Machine Learning](https://www.amazon.com/Dataset-Machine-Learning-Information-Processing/dp/0262170051), is literally a textbook summarizing previous contributions. I find their lack of attribution downright shameful. [Domain Adaptation under Target and Conditional Shift
](http://proceedings.mlr.press/v28/zhang13d.html) is a fantastic article published 5 years before Prior Networks.

## Section 7: Future Work

Criticisms aside, the core challenged identified in Prior Networks of how the total uncertainty for new data depends on different sources of uncertainty is a significant problem without provably good solutions, especially for classifiers that use deep neural networks. Several possible future directions exist:

1. Extend this work to regression problems, where the network outputs parameters for the distribution of the target value. For example, for a given input $x$ with target value $y$, we might implement the model to output a mean $\mu$ and covariance $\Sigma$ that parameterize the distribution of y i.e. $y \sim N(\mu, \Sigma)$.

2. Remove the necessity of training on out-of-distribution data. Requiring that the model be trained on out-of-distribution data requires defining (or at least sampling from) $p(\neg x, \neg y) \cup p(x, \neg y) \cup p(\neg x, y)$, a problem that is typically at least as hard as defining $p(x,y)$ in the first place, if not harder since there are typically many more elements outside $p(x, y)$ than inside it.

3. Estimate distributional uncertainty better by using density estimation methods. For example, [recent work](https://arxiv.org/abs/1912.03263) suggested that classifiers $p(y|x)$ can be converted to density estimation $p(x, y)$ through an energy-based framework; alternatively, unsupervised learning techniques like variational autoencoders [can be used to learn the geometric structure of the data](https://pdfs.semanticscholar.org/57e1/7ce6e9a06aa8137ea355ba53073e3ffc7de6.pdf).